In [2]:
%matplotlib inline
from pycocotools.coco import COCO
import numpy as np
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
pylab.rcParams['figure.figsize'] = (8.0, 10.0)

#looking at images (and their annotations) in the val2017 folder
dataDir='..'
dataType='val2017'
annFile='{}/annotations/instances_{}.json'.format(dataDir,dataType)

# initialize COCO api for instance annotations
coco=COCO(annFile);


#dataTypes = ["val2017","train2014","val2014","test2014","test2015","train2017","test2017"]
dataTypes = ["val2017","test2015","train2017","test2017"]

valid_categories=[cat['name'] for cat in coco.loadCats(coco.getCatIds())];

loading annotations into memory...
Done (t=0.45s)
creating index...
index created!


In [3]:
def boundaries(bbox):#function for extracting bounding box from bbox class found in each image
    return {'ymax':bbox[1],'ymin':(bbox[3]+bbox[1]),'xmin':bbox[0],'xmax':(bbox[0]+bbox[2])}

In [13]:
def getAnnFile(imgFolder):
    instances = ["val2017","train2014","val2014","train2017"]
    tests = ["test2014","test2015","test2017"]
    if imgFolder in instances:
        dataDir='..'
        dataType=imgFolder
        return '{}/annotations/instances_{}.json'.format(dataDir,dataType)
    elif imgFolder in tests:
        dataDir='..'
        dataType=imgFolder
        return '{}/annotations/image_info_{}.json'.format(dataDir,dataType)
    else:
        print(imgFolder + "'s annotation file is not accounted for in this dictionary")
        return
    

In [14]:
#create xml for an image for 1st plane
from lxml import etree as e

def build_folder_xmls(imgFolder,category):
     #confirm category and image folder exist
    if(not(imgFolder in dataTypes)):
        print("Folder does not exist in Images")
        return
    if(not(category in valid_categories)):
        print("Catergory does not exist in COCO database")
        return
    
    #reload coco API 
    dataDir='..'
    dataType=imgFolder
    #annFile='{}/annotations/instances_{}.json'.format(dataDir,dataType)
    annFile = getAnnFile(imgFolder)
    
    # initialize COCO api for instance annotations
    coco=COCO(annFile);
    
    # get all the catergory's image file_names
    catIds = coco.getCatIds(catNms=[category]);
    imgIds = coco.getImgIds(catIds=catIds );
    
    #write subfunction that will use these parameters
    def build_xml(i):



        #load image data
        img = coco.loadImgs(imgIds[i])[0]

        #build xml
        root = e.Element('annotation')

        folder = e.Element('folder')
        folder.text="images"
        root.append(folder)

        file = e.Element('filename')
        file.text=img['file_name']
        root.append(file)

        size = e.Element('size')
        width = e.Element('width')
        width.text = str(img['width'])
        height = e.Element('height')
        height.text = str(img['height'])
        depth = e.Element('depth')
        depth.text="3"
        size.append(width)
        size.append(height)
        size.append(depth)
        root.append(size)

        seg = e.Element('segmented')
        seg.text = "0"
        root.append(seg)

        annIds = coco.getAnnIds(imgIds=img['id'], catIds=catIds, iscrowd=None)
        anns = coco.loadAnns(annIds)
        for i in range(0,len(anns)):
            #bounding values for one plane
            bbox = anns[i]['bbox']
            bounds = boundaries(bbox)

            #Header info for each plane
            obj = e.Element('object')
            name = e.Element('name')
            name.text=category
            pose = e.Element('pose')
            pose.text = 'Unspecified'
            truncated = e.Element('truncated')
            truncated.text='0'
            difficult = e.Element('difficult')
            difficult.text='0'
            obj.append(name)
            obj.append(pose)
            obj.append(truncated)
            obj.append(difficult)

            #bounding box
            bndbox = e.Element('bndbox')
            xmin = e.Element('xmin')
            xmin.text = str(bounds['xmin'])

            ymin = e.Element('ymin')
            ymin.text = str(bounds['ymin'])

            xmax = e.Element('xmax')
            xmax.text = str(bounds['xmax'])

            ymax = e.Element('ymax')
            ymax.text = str(bounds['ymax'])

            bndbox.append(xmin)
            bndbox.append(ymin)
            bndbox.append(xmax)
            bndbox.append(ymax)

            obj.append(bndbox)

            root.append(obj)






        #root.append(e.Element('folder'))

        s= e.tostring(root,pretty_print=True)
        #s=str(e)
        print(s)

        f=open(("{}/xml_converted/"+category+"/" + img['file_name'][0:(len(img['file_name'])-4)]+'.xml').format(dataDir,dataType),'wb')
        f.write(s)
        f.close()
    
    #call sub-funtion on every element of the set of images
    for i in range(0,len(imgIds)):
        build_xml(i);


In [20]:
#copy all images in a category out
from shutil import copyfile


def copy_category_images(imgFolder,category):
    #confirm category and image folder exist
    if(not(imgFolder in dataTypes)):
        print("Folder does not exist in Images")
        return
    if(not(category in valid_categories)):
        print("Catergory does not exist in COCO database")
        return
    
    #re-build coco-API
    dataDir='..'
    dataType=imgFolder
    #annFile='{}/annotations/instances_{}.json'.format(dataDir,dataType)
    annFile = getAnnFile(imgFolder)
    
    # initialize COCO api for instance annotations
    coco=COCO(annFile);
    
    # get all the catergory's image file_names
    catIds = coco.getCatIds(catNms=[category]);
    imgIds = coco.getImgIds(catIds=catIds );
    
    #copy images
    for i in range (0,len(imgIds)):
        img = coco.loadImgs(imgIds[i])[0]
        png =img['file_name']
        src =('{}/images/'+imgFolder+'/'+ png).format(dataDir,dataType)
        dst =('{}/categorized_images/'+category+"/"+png).format(dataDir,dataType)
        copyfile(src,dst)

In [16]:
build_folder_xmls("val2017","airplane");

loading annotations into memory...
Done (t=0.30s)
creating index...
index created!
b'<annotation>\n  <folder>images</folder>\n  <filename>000000208901.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>427</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>232.67</xmin>\n      <ymin>284.59000000000003</ymin>\n      <xmax>425.99</xmax>\n      <ymax>148.37</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>000000090631.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>389</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>176.77</xmin>\n      <ymin>228.1700000000000

In [17]:
copy_category_images("val2017","airplane");

loading annotations into memory...
Done (t=0.31s)
creating index...
index created!


In [ ]:
copy_category_images("val2017","bird");

In [ ]:
build_folder_xmls("val2017","bird");

In [21]:

def xml_category(category):
    for folder in dataTypes:
        build_folder_xmls(folder,category)
def image_category(category):
    for folder in dataTypes:
        copy_category_images(folder,category)
def convert_category(category):
    xml_category(category)
    image_category(category)
    

In [19]:
import time
start = time.time()
convert_category("airplane") #not possible until all folders downloaded
print("finished in "+str(time.time()-start)+" seconds")

loading annotations into memory...
Done (t=0.51s)
creating index...
index created!
b'<annotation>\n  <folder>images</folder>\n  <filename>000000208901.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>427</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>232.67</xmin>\n      <ymin>284.59000000000003</ymin>\n      <xmax>425.99</xmax>\n      <ymax>148.37</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>000000090631.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>389</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>176.77</xmin>\n      <ymin>228.1700000000000

Done (t=8.68s)
creating index...
index created!
b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000221184.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>426</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>7.51</xmin>\n      <ymin>403.82</ymin>\n      <xmax>640.0</xmax>\n      <ymax>27.18</ymax>\n    </bndbox>\n  </object>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>1.73</xmin>\n      <ymin>306.85</ymin>\n      <xmax>217.35999999999999</xmax>\n      <ymax>244.57</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000393221.jpg</filename>\n  <size>\n    <width>427</width>\n    <height>640</h

b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000361275.jpg</filename>\n  <size>\n    <width>500</width>\n    <height>333</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>40.32</xmin>\n      <ymin>62.56</ymin>\n      <xmax>53.32</xmax>\n      <ymax>55.06</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000262980.jpg</filename>\n  <size>\n    <width>500</width>\n    <height>333</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>10.43</xmin>\n      <ymin>193.05</ymin>\n      <xmax>465.6</xmax>\n      <ymax>102.17</ymax>\n    </bndbox>\n  </

b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000394784.jpg</filename>\n  <size>\n    <width>496</width>\n    <height>640</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>14.32</xmin>\n      <ymin>379.62</ymin>\n      <xmax>418.08</xmax>\n      <ymax>160.56</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000157219.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>480</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>0.0</xmin>\n      <ymin>403.48999999999995</ymin>\n      <xmax>626.7</xmax>\n      <ymax>1.15</ymax>\n    </bn

b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000125494.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>478</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>90.89</xmin>\n      <ymin>388.33</ymin>\n      <xmax>567.83</xmax>\n      <ymax>260.01</ymax>\n    </bndbox>\n  </object>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>452.61</xmin>\n      <ymin>370.02000000000004</ymin>\n      <xmax>580.71</xmax>\n      <ymax>339.22</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>COCO_train2014_000000510521.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>418</height>\n    <depth>3</depth>\n  </size>\n  

...

b'<annotation>\n  <folder>images</folder>\n  <filename>000000121302.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>569</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>11.48</xmin>\n      <ymin>382.23</ymin>\n      <xmax>625.13</xmax>\n      <ymax>209.99</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>000000219606.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>359</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>382.4</xmin>\n      <ymin>154.65</ymin>\n      <xmax>639.75</xmax>\n      <ymax>17.5</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'

b'<annotation>\n  <folder>images</folder>\n  <filename>000000129940.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>427</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>262.97</xmin>\n      <ymin>220.69</ymin>\n      <xmax>330.45000000000005</xmax>\n      <ymax>159.79</ymax>\n    </bndbox>\n  </object>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>116.13</xmin>\n      <ymin>118.73</ymin>\n      <xmax>184.89</xmax>\n      <ymax>59.17</ymax>\n    </bndbox>\n  </object>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>228.14</xmin>\n      <ymin>262.14</ymin>\n      <xmax>296.76</xmax>\n  

b'<annotation>\n  <folder>images</folder>\n  <filename>000000261645.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>427</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>295.32</xmin>\n      <ymin>291.77</ymin>\n      <xmax>531.5699999999999</xmax>\n      <ymax>72.94</ymax>\n    </bndbox>\n  </object>\n</annotation>\n'
b'<annotation>\n  <folder>images</folder>\n  <filename>000000146959.jpg</filename>\n  <size>\n    <width>640</width>\n    <height>553</height>\n    <depth>3</depth>\n  </size>\n  <segmented>0</segmented>\n  <object>\n    <name>airplane</name>\n    <pose>Unspecified</pose>\n    <truncated>0</truncated>\n    <difficult>0</difficult>\n    <bndbox>\n      <xmin>211.97</xmin>\n      <ymin>395.47</ymin>\n      <xmax>416.12</xmax>\n      <ymax>280.68</ymax>\n    </bndbox>\n  </object>\n  <ob

loading annotations into memory...
Done (t=0.13s)
creating index...
index created!
loading annotations into memory...
Done (t=0.32s)
creating index...
index created!
loading annotations into memory...
Done (t=8.24s)
creating index...
index created!
loading annotations into memory...
Done (t=3.79s)
creating index...
index created!
loading annotations into memory...


FileNotFoundError: [Errno 2] No such file or directory: '../annotations/instances_test2014.json'

In [22]:
import time
start = time.time()
image_category("airplane") #not possible until all folders downloaded
print("finished in "+str(time.time()-start)+" seconds")

loading annotations into memory...
Done (t=0.40s)
creating index...
index created!
loading annotations into memory...
Done (t=8.36s)
creating index...
index created!
loading annotations into memory...
Done (t=3.57s)
creating index...
index created!
loading annotations into memory...
Done (t=0.07s)
creating index...
index created!
loading annotations into memory...
Done (t=0.14s)
creating index...
index created!
loading annotations into memory...
Done (t=12.99s)
creating index...
index created!
loading annotations into memory...
Done (t=0.05s)
creating index...
index created!
finished in 174.2782382965088 seconds
